# JACKET V1 のデータセットに　wikipedia のコンテキストを追加したデータセットの作成

- https://sites.google.com/view/project-aio/dataset?authuser=0

の CC BY-SA 4.0 DEED 該当データをもとに、Wikipedia のコンテキスト追加した HuggingFace Dataset を作成する


In [1]:
# JAQKET データセットを取得

from dataclasses import dataclass
import json
import urllib.request
import random

random.seed(42)

# https://sites.google.com/view/project-aio/dataset?authuser=0
# 以下のURLのデータは、ライセンスが CC BY-SA 4.0 DEED

jaqket_urls = [
    "https://jaqket.s3.ap-northeast-1.amazonaws.com/data/aio_02/aio_01_dev.jsonl",
    "https://jaqket.s3.ap-northeast-1.amazonaws.com/data/aio_02/aio_01_test.jsonl",
    "https://jaqket.s3.ap-northeast-1.amazonaws.com/data/aio_02/aio_01_unused.jsonl",
]


@dataclass
class JaqketQuestion_:
    qid: str
    question: str
    original_question: str
    answer_entity: str
    answer_candidates: list[str]
    answer_candidates_shuffled: list[str]
    label: int
    original_answer: str | None = None


@dataclass
class JaqketQuestion:
    qid: str
    competition: str
    timestamp: str
    section: str
    number: str
    original_question: str
    original_answer: str | None
    original_additional_info: str | None
    question: str
    answers: list[str]


def load_jaqket(urls: list[str]):
    res = []
    for url in urls:
        with urllib.request.urlopen(url) as f:
            # f は 1行ごとに処理
            data = [json.loads(line.decode("utf-8")) for line in f]
        for d in data:
            try:
                res.append(JaqketQuestion(**d))
            except Exception as e:
                # d.keys
                print(d.keys())
                raise e
    return res


jacket_data = load_jaqket(jaqket_urls)

In [2]:
import pandas as pd

jacket_df = pd.DataFrame(jacket_data)
jacket_df.shape

(4600, 10)

In [3]:
# none は "" に変換
jacket_df = jacket_df.fillna("")
# answers の最初の一つを入れる
jacket_df.loc[:, "answer"] = jacket_df["answers"].apply(lambda x: x[0])
jacket_df.head(1)

qid competition   timestamp         section number  \
0  QA20CAPR-0002      第1回AI王  2019/12/25  開発データ問題 (dev1)      2   

                                   original_question original_answer  \
0  明治時代に西洋から伝わった「テーブル・ターニング」に起源を持つ占いの一種で、50音表などを記...          コックリさん   

  original_additional_info                                           question  \
0                           明治時代に西洋から伝わった「テーブル・ターニング」に起源を持つ占いの一種で、50音表などを記...   

    answers  answer  
0  [コックリさん]  コックリさん

In [4]:
train_df = jacket_df

In [5]:
from datasets.download import DownloadManager
from datasets import load_dataset
from sentence_transformers import SentenceTransformer
import faiss

# wikipedia 日本語データセットのロード
wikija_dataset = load_dataset(
    path="singletongue/wikipedia-utils",
    name="passages-c400-jawiki-20230403",
    split="train",
)
# faiss index のダウンロード
dm = DownloadManager()
index_local_path = dm.download(
    f"https://huggingface.co/datasets/hotchpotch/wikipedia-passages-jawiki-embeddings/resolve/main/faiss_indexes/passages-c400-jawiki-20230403/multilingual-e5-large-query/index_IVF2048_PQ256.faiss"
)
# index_local_path = dm.download(
#     f"https://huggingface.co/datasets/hotchpotch/wikipedia-passages-jawiki-embeddings/resolve/main/faiss_indexes/passages-c400-jawiki-20230403/multilingual-e5-large-passage/index_IVF2048_PQ256.faiss"
# )
# faiss index のロード
faiss_index = faiss.read_index(index_local_path)

# embeddings へ変換するモデルのロード
emb_model = SentenceTransformer("intfloat/multilingual-e5-large", device="cuda")
emb_model.max_seq_length = 512

/home/yu1/miniconda3/envs/llm-sc/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [6]:
# embeddings へ変換
def texts_to_embs(model, texts, prefix="query: "):
    texts = [prefix + text for text in texts]
    return model.encode(texts, normalize_embeddings=True)


texts_to_embs(emb_model, ["こんにちは", "こんばんは"]).shape

(2, 1024)

In [7]:
# wikipedia のデータから、RAG検索して Top-N に正解の単語が含まれているデータのみを抽出する


def df_correct_answer_add_context(df, top_n=3):
    # faiss index で検索して、top-N に正解があれば、その context を追加してそのデータのみを返す
    df = df.copy().reset_index(drop=True)
    df["context"] = None
    texts = df["question"].tolist()
    embs = texts_to_embs(emb_model, texts)
    scores, indexes = faiss_index.search(embs, top_n)
    for pos, (score, index) in enumerate(zip(scores, indexes)):
        df_data = df.iloc[pos]
        answer = df_data["answer"]
        target_texts = []
        for s, i in zip(score, index):
            data = wikija_dataset[int(i)]  # type: ignore
            target_texts.append(data["title"] + " " + data["text"])  # type: ignore
        check_text = str(target_texts)
        # 検索結果に対象文字列を含むか
        if answer in check_text:
            df.at[pos, "context"] = target_texts
    # top3_text が None でないデータのみ返す
    return df[df["context"].notnull()]


train_df = df_correct_answer_add_context(train_df, 3)
train_df.shape

(3919, 12)

In [8]:
# qid, question, answer, context が先頭のカラムに来るように並び替える。過去のカラムも残す
new_columns = ["qid", "question", "answer", "context", "answers"]
new_columns.extend([c for c in train_df.columns if c not in new_columns])
train_df = train_df[new_columns]
train_df.head(1)

qid                                           question  answer  \
0  QA20CAPR-0002  明治時代に西洋から伝わった「テーブル・ターニング」に起源を持つ占いの一種で、50音表などを記...  コックリさん   

                                             context   answers competition  \
0  [コックリさん その起源は明確ではないが、レオナルド・ダ・ヴィンチが自著において「テーブル・...  [コックリさん]      第1回AI王   

    timestamp         section number  \
0  2019/12/25  開発データ問題 (dev1)      2   

                                   original_question original_answer  \
0  明治時代に西洋から伝わった「テーブル・ターニング」に起源を持つ占いの一種で、50音表などを記...          コックリさん   

  original_additional_info  
0

In [9]:
import datasets

# pandas to dataset
train_dataset = datasets.Dataset.from_pandas(train_df)

In [10]:
train_dataset

Dataset({
    features: ['qid', 'question', 'answer', 'context', 'answers', 'competition', 'timestamp', 'section', 'number', 'original_question', 'original_answer', 'original_additional_info', '__index_level_0__'],
    num_rows: 3919
})

In [11]:
# 25% を validation にする
valid_df = train_df.sample(frac=0.25, random_state=42)
train_df = train_df.drop(valid_df.index)
train_df = train_df.reset_index(drop=True)
valid_df = valid_df.reset_index(drop=True)
# shape
train_df.shape, valid_df.shape

((2939, 12), (980, 12))

In [12]:
from datasets import Dataset

train_ds = Dataset.from_pandas(train_df)
valid_ds = Dataset.from_pandas(valid_df)

In [13]:
dataset_hf_path = "hotchpotch/jaqket_v1_qa_wikija_context"

In [16]:
train_ds.push_to_hub(dataset_hf_path, split="train")
valid_ds.push_to_hub(dataset_hf_path, split="validation")

README.md: 100%|██████████| 715/715 [00:00<00:00, 3.93MB/s]
